In [1]:
import csv

from prompt_toolkit.utils import to_float


In [2]:
# ToDo: Materialized View für Mittel aus mehreren Vollsätzen verschiedener Standpunkte erstellen und nach dem importieren der Tachymeterdaten aaktualisieren (Dazu klären: Wo werden die Gewichte der einzelnen Beobachtungen gespeichert?)

# Hier werden die Nutzereingaben vorgenommen:
pfad_datenbank = r"C:\Users\fabia\OneDrive\Jade HS\Master\MGW2\Masterprojekt_allgemein\Masterprojekt\Programmierung\Campusnetz\Campusnetz.db"

In [3]:
# Es wird geprüft, ob die .db-Datei bereits vorhanden ist. Wenn dies nicht der Fall ist, wird die Datenbank mitsamt aller Tabellen angelegt.
Datenbank.Datenbank_anlegen(pfad_datenbank)
pfad = r"C:\Users\fabia\OneDrive\Jade HS\Master\MGW2\Masterprojekt_allgemein\Masterprojekt\Übungsnetz\Tachymeterdaten\Masterprobe_2.csv"

In [ ]:
# ToDo: Dateipfad bereits vorhanden? --> Abbruch import
# ToDo: Rundungsfehler überarbeiten!
# ToDo: Print ausgabe Anzahl importierte Punkte
# ToDo: Ggf. Ausgabe Rohdaten in Tabellenform (Berechnungen nachvollziehen)

import sqlite3

liste_netzpunkte = []
liste_netzpunkte_neu = []
liste_netzpunkte_vorhanden = []
liste_zeilennummern_Orientierung = []
liste_standpunkte = []
liste_beobachtungen = []

with open (pfad, newline='', encoding='utf-8') as csvfile:
    r = csv.reader(csvfile, delimiter=';')
    zeilennummer = 0
    for row in r:
        zeilennummer += 1
        if zeilennummer < 4:
            pass
        else:
            if row[0] != "Orientierung":
                liste_netzpunkte.append(row[0].strip())
            else:
                liste_zeilennummern_Orientierung.append(zeilennummer-1)
                liste_standpunkte.append(zeilennummer-1)
                liste_zeilennummern_Orientierung.append(zeilennummer)
           #print(row)


liste_netzpunkte = list(set(liste_netzpunkte))

con = sqlite3.connect(pfad_datenbank)
cursor = con.cursor()
cursor.execute("""SELECT punktnummer FROM Netzpunkte""")
liste_netzpunkte_in_db = {row[0] for row in cursor.fetchall()}

liste_netzpunkte_neu = [np for np in liste_netzpunkte if np not in liste_netzpunkte_in_db]
liste_netzpunkte_vorhanden = [np for np in liste_netzpunkte if np in liste_netzpunkte_in_db]

for np_neu in liste_netzpunkte_neu:
    cursor.execute("INSERT INTO Netzpunkte (punktnummer) VALUES (?)", (np_neu,))

with open (pfad, newline='', encoding='utf-8') as csvfile:
    r = csv.reader(csvfile, delimiter=';')
    standpunktsnummer = 0
    for nummer, row in enumerate(r, start=1):
        if nummer < 4:
            pass
        if nummer in liste_zeilennummern_Orientierung:
            if row[0] != "Orientierung":
                punktnummer = row[0].strip()
            else:
                standpunktsnummer += 1
                cursor.execute("INSERT INTO Standpunkte_Tachymeter (punktnummer, orientierunghz, orientierungv, dateipfad, standpunktsnummer) VALUES (?, ?, ?, ?, ?)", (punktnummer, row[1], row[2], pfad, standpunktsnummer))

with open (pfad, newline='', encoding='utf-8') as csvfile:
    r = csv.reader(csvfile, delimiter=';')
    rows = list(r)

    for index, row in enumerate(liste_standpunkte):
        zeile_punktnummer = row - 1
        punktnummer = rows[zeile_punktnummer][0].strip()
        zeile_eins = zeile_punktnummer + 2
        if index + 1 < len(liste_standpunkte):
            zeile_zwei = liste_standpunkte[index + 1]
        else:
            zeile_zwei = len(rows)+1

        for i in range (zeile_eins, zeile_zwei-1):
            liste_beobachtungen.append([punktnummer] + rows[i])

    standpunktsnummer = 0
    standpunkt_alt = None
while len(liste_beobachtungen) > 0:
    standpunkt1 = liste_beobachtungen[0][0]
    zielpunkt1 = liste_beobachtungen[0][1]
    horizonalwinkel1 = to_float(liste_beobachtungen[0][2].replace(',', '.'))
    vertikalwinkel1 = to_float(liste_beobachtungen[0][3].replace(',', '.'))
    distanz1 = to_float(liste_beobachtungen[0][4].replace(',', '.'))
    liste_beobachtungen.pop(0)

    if standpunkt_alt != standpunkt1:
        standpunktsnummer += 1

    standpunkt_alt = standpunkt1

    standpunktsid = cursor.execute("SELECT spID FROM Standpunkte_Tachymeter WHERE punktnummer = ? AND dateipfad = ? AND standpunktsnummer = ?", (standpunkt1, pfad, standpunktsnummer)).fetchall()[0][0]

    index_beobachtung2 = None
    for index in range(len(liste_beobachtungen)):
        beobachtung = liste_beobachtungen[index]
        if beobachtung[0] == standpunkt1 and beobachtung[1] == zielpunkt1:
            index_beobachtung2 = index
            break
    if index_beobachtung2 is None:
        print(f"Zweite Lage für Standpunkt: {standpunkt1}, Zielpunkt: {zielpunkt1} wurde nicht gefund!")

    standpunkt2 = liste_beobachtungen[index_beobachtung2][0]
    zielpunkt2 = liste_beobachtungen[index_beobachtung2][1]
    horizonalwinkel2 = to_float(liste_beobachtungen[index_beobachtung2][2].replace(',', '.'))
    vertikalwinkel2 = to_float(liste_beobachtungen[index_beobachtung2][3].replace(',', '.'))
    distanz2 = to_float(liste_beobachtungen[index_beobachtung2][4].replace(',', '.'))

    if horizonalwinkel1 > horizonalwinkel2:
        horizontalwinkel_vollsatz = (horizonalwinkel1 + horizonalwinkel2 + 200) / 2
    else:
        horizontalwinkel_vollsatz = (horizonalwinkel1 + horizonalwinkel2) / 2

    if vertikalwinkel1 < vertikalwinkel2:
        vertikalwinkel_satzmittel = (400 + (vertikalwinkel1 - vertikalwinkel2)) / 2
    else:
        vertikalwinkel_satzmittel = (400 + (vertikalwinkel2 - vertikalwinkel1)) / 2

    distanz_satzmittel = (distanz1 + distanz2) / 2

    print(f"spid: {standpunktsid}, standpunktsnummer: {standpunktsnummer},standpunkt1: {standpunkt1}, standpunkt2: {standpunkt2}, zielpunkt1: {zielpunkt1}, zielpunkt2: {zielpunkt2}, horizonalwinkel1: {horizonalwinkel1}, horizonalwinkel2: {horizonalwinkel2}, horizontalwinkel_vollsatz: {horizontalwinkel_vollsatz},vertikalwinkel1: {vertikalwinkel1}, vertikalwinkel2: {vertikalwinkel2}, vertikalwinkel_vollsatz: {vertikalwinkel_satzmittel},distanz1: {distanz1}, distanz2: {distanz2}, distanz_satzmittel: {distanz_satzmittel}")

    liste_beobachtungen.pop(index_beobachtung2)

    cursor.execute("INSERT INTO Beobachtungen_Tachymeter (spID, punktnummer, hz, v, distanz) VALUES (?, ?, ?, ?, ?)", (standpunktsid, standpunkt1, horizontalwinkel_vollsatz, vertikalwinkel_satzmittel, distanz_satzmittel))

        #print(row)
    #print(len(liste_standpunkte))
    #print(len(list(r)))


con.commit()
con.close()


print(liste_beobachtungen)
print(f"Es wurden {len(liste_netzpunkte_neu)} neue Punkte importiert. Dies sind: {', '.join(map(str, liste_netzpunkte_neu))}")
print(f"Es sind bereits {len(liste_netzpunkte_vorhanden)} Punkte im Netz enthalten. Dies sind: {', '.join(map(str, liste_netzpunkte_vorhanden))}")
# ToDo: Näherungswerte für Koordinaten aus Tychymetermessungen berechnen
# ToDo: Wenn GNSS-Daten vorliegen: Koordinaten von GNSS verwenden!